<a href="https://colab.research.google.com/github/felipednegredo/tcc-emocoes-musicais-codigo/blob/main/TCC_Fingerprint_Shazam.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
pip install -q -U kaleido pyarrow fastparquet

In [ ]:
# ===============================================================
#  FINGERPRINT em LOTE (blocks_by_song/*.parquet) — Shazam-like
#  - STFT (detecção de dB automático) + contraste estável
#  - Picos: densidade alvo + TOP-K por banda + equalização opcional
#  - Fan-out: âncora + linhas (sem Target Zone)
#  - Exporta: HTML por bloco e PARQUET com picos por música
#  - Fundo branco, ticks de X controlados, barras de progresso
# ===============================================================

import os, re, io, zlib, math, time, warnings, pathlib
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import librosa
warnings.filterwarnings("ignore")

# ------------- tqdm (progress bar) -------------
try:
    from tqdm.auto import tqdm
except Exception:
    tqdm = None

try:
    from scipy.ndimage import median_filter
    SCIPY_OK = True
except Exception:
    SCIPY_OK = False

# ==================== CONFIG ====================
# Aceita diretório (varre *.parquet) ou um único arquivo
IN_PATH       = "/content/drive/MyDrive/DataSet TCC/DEAM/parquet/blocks_by_song"
OUT_ROOT      = "/content/drive/MyDrive/DataSet TCC/DEAM/fingerprint"

# Renderização (ambas independentes)
DO_DUAL       = True     # STFT | Constellation
DO_OVERLAY    = True     # STFT + Constellation

EXPORT_HTML   = True     # exporta HTML (sempre disponível)
IMG_W, IMG_H  = 1280, 640

# Visual
YLIM_HZ       = (50, 8000)
USE_LOG_Y     = False
SPEC_CMAP     = "Inferno"
ZLIM_FIXED    = (-75, 0)
TITLE_PREFIX  = "Fingerprint espectral — "

# Picos (bandas + TOP-K)
BANDS              = [(80,300), (300,1200), (1200,4000), (4000,8000)]
TOPK_PER_BAND      = 1

# Equalização para detecção (opcional)
EQUALIZE_FOR_PEAKS = True
EQ_SIZE_FREQ       = 15

# Controle de densidade (busca binária no percentil global)
AUTO_PEAK_DENSITY     = True
TARGET_PEAKS_PER_SEC  = 20.0
PCTL_SEARCH_RANGE     = (80.0, 99.9)
MAX_BINSEARCH_ITERS   = 12
TOLERANCE_RELATIVE    = 0.20

# Fan-out (âncora central + linhas)
SHOW_FAN_LINES  = True
FAN_T_MIN       = 0.02
FAN_T_MAX       = 0.50
FAN_FANOUT      = 6

# Eixo X (ticks em passo fixo)
X_TICK_STEP_BASE = 2.0  # segundos

# Símbolo dos picos (estilo artigo)
PK_MARKER = dict(symbol="x", size=7, opacity=0.9,
                 color="#000000", line=dict(width=1.2, color="#111111"))

# =================== HELPERS ====================
def ensure_dir(p): pathlib.Path(p).mkdir(parents=True, exist_ok=True)

def slugify(s):
    s = (s or "desconhecida").strip().lower()
    s = re.sub(r"[^\w\s-]+", "", s); s = re.sub(r"\s+", "_", s)
    return s[:60] or "sem_titulo"

def bytes_to_ndarray(b):
    if b is None: return np.array([])
    if isinstance(b, (bytes, bytearray)):
        try:
            raw = zlib.decompress(b)
            return np.load(io.BytesIO(raw), allow_pickle=False)
        except Exception:
            return np.load(io.BytesIO(b), allow_pickle=False)
    if isinstance(b, np.ndarray): return b
    return np.array([])

def _nice_tick_params(times: np.ndarray):
    """
    Ticks em múltiplos de X_TICK_STEP_BASE, adaptados à duração.
    """
    if times is None or times.size == 0:
        return dict(dtick=X_TICK_STEP_BASE, tick0=0.0)
    t0 = float(np.nanmin(times)); t1 = float(np.nanmax(times))
    dur = max(t1 - t0, 0.0)
    step = X_TICK_STEP_BASE
    if dur > 60:   step = 5 * X_TICK_STEP_BASE
    if dur > 300:  step = 10 * X_TICK_STEP_BASE
    tick0 = math.floor(t0 / step) * step
    return dict(dtick=step, tick0=tick0)

def detect_scale_and_fix(S, freqs, times, zlim_fixed=ZLIM_FIXED):
    """
    - Garante orientação (freq x frames) quando possível
    - Detecta se S já está em dB (evita re-log)
    - Corrige NaN/Inf
    - Retorna S_db, freqs, times, (zmin,zmax)
    """
    if S is None or S.size == 0:
        raise ValueError("detect_scale_and_fix: matriz S vazia.")
    S = np.array(S, copy=False)

    # Orientação
    try:
        if freqs.size and times.size and S.shape[0] == times.size and S.shape[1] == freqs.size:
            S = S.T
    except Exception:
        pass

    # Sanitização
    S = np.where(np.isfinite(S), S, np.nan)
    if np.isnan(S).all():
        raise ValueError("detect_scale_and_fix: S só contém NaN/Inf.")
    finite_min = float(np.nanmin(S))
    S = np.nan_to_num(S, nan=finite_min)

    # Escala
    S_min, S_max = float(np.min(S)), float(np.max(S))
    frac_neg = float((S < 0).mean()) if S.size else 0.0
    is_db_like = ((S_max <= 5.0 and S_min < -10.0) or (frac_neg > 0.6))

    if np.iscomplexobj(S):
        S_abs = np.abs(S); is_db_like = False
    else:
        S_abs = np.abs(S)

    if is_db_like:
        S_db = S.astype(float, copy=False)
    else:
        ref = np.max(S_abs) if np.max(S_abs) > 0 else 1.0
        S_db = librosa.amplitude_to_db(S_abs, ref=ref)

    # freqs/times default
    if freqs is None or (isinstance(freqs, np.ndarray) and freqs.size == 0):
        freqs = np.linspace(0.0, 22050.0, S_db.shape[0], dtype=float)
    if times is None or (isinstance(times, np.ndarray) and times.size == 0):
        times = np.arange(S_db.shape[1], dtype=float)

    # z-limits
    if zlim_fixed is not None and len(zlim_fixed) == 2:
        zmin, zmax = zlim_fixed
    else:
        zmin, zmax = np.nanpercentile(S_db, [1, 99])
    return S_db, np.asarray(freqs, float), np.asarray(times, float), (float(zmin), float(zmax))

def equalize_for_peaks(S_db):
    if not SCIPY_OK or EQ_SIZE_FREQ <= 1: return S_db
    return S_db - median_filter(S_db, size=(EQ_SIZE_FREQ, 1))

# -------- picos por percentil FIXO (base p/ busca binária) --------
def _peaks_with_percentile(S_db, freqs, times, pctl):
    """
    Seleciona picos por coluna com threshold = percentil(pctl) + TOP-K por banda.
    Retorna (pt, pf).
    """
    if S_db is None or S_db.size == 0:
        return np.array([]), np.array([])
    freqs = np.asarray(freqs) if isinstance(freqs, np.ndarray) else np.array(freqs)
    times = np.asarray(times) if isinstance(times, np.ndarray) else np.array(times)
    if freqs.size == 0:
        freqs = np.linspace(0.0, 22050.0, S_db.shape[0], dtype=float)
    if times.size == 0:
        times = np.arange(S_db.shape[1], dtype=float)

    n_freq, n_frames = S_db.shape
    pk_t, pk_f = [], []

    S_for = equalize_for_peaks(S_db) if EQUALIZE_FOR_PEAKS else S_db
    thr_cols = np.percentile(S_for, pctl, axis=0)  # shape (n_frames,)

    for t in range(n_frames):
        col = S_for[:, t]
        thr = float(thr_cols[t])
        for (lo, hi) in BANDS:
            band = (freqs >= lo) & (freqs < hi)
            idxs = np.where((col >= thr) & band)[0]
            if idxs.size == 0:
                continue
            sel = idxs[np.argsort(col[idxs])[::-1][:TOPK_PER_BAND]]
            pk_t.extend([times[t]] * len(sel))
            pk_f.extend(freqs[sel].tolist())

    return np.asarray(pk_t), np.asarray(pk_f)

# -------- picos com densidade-alvo --------
def estimate_peaks_auto_density(S_db, freqs, times,
                                target_pps=TARGET_PEAKS_PER_SEC):
    """
    Ajusta o percentil global via busca binária para atingir ~target_pps (picos/seg),
    mantendo TOP-K por banda.
    """
    if S_db is None or S_db.size == 0:
        return np.array([]), np.array([])
    freqs = np.asarray(freqs) if isinstance(freqs, np.ndarray) else np.array(freqs)
    times = np.asarray(times) if isinstance(times, np.ndarray) else np.array(times)
    if times.size == 0:
        times = np.arange(S_db.shape[1], dtype=float)

    dur = max(float(np.nanmax(times) - np.nanmin(times)), 1e-6)
    target_total = int(target_pps * dur)

    lo, hi = PCTL_SEARCH_RANGE
    best_pt, best_pf = np.array([]), np.array([]); best_diff = float("inf")

    for _ in range(MAX_BINSEARCH_ITERS):
        mid = (lo + hi) / 2.0
        pt, pf = _peaks_with_percentile(S_db, freqs, times, pctl=mid)
        n = int(pt.size)
        diff = abs(n - target_total)
        if diff < best_diff:
            best_diff, best_pt, best_pf = diff, pt, pf
        # tolerância
        if target_total == 0 or abs(n - target_total) / max(target_total, 1) <= TOLERANCE_RELATIVE:
            break
        # direção
        if n > target_total:   # muitos picos → sobe percentil
            lo = mid
        else:                  # poucos picos → desce percentil
            hi = mid

    return best_pt, best_pf

def select_anchor_and_targets(pt, pf):
    """
    Escolhe uma âncora (mediana temporal) e seleciona até FAN_FANOUT alvos
    no intervalo (t_a + FAN_T_MIN, t_a + FAN_T_MAX).
    """
    if pt.size == 0 or pf.size == 0:
        return None, []
    idx_sorted = np.argsort(pt)
    i = idx_sorted[len(idx_sorted)//2]  # posição mediana
    t_a, f_a = float(pt[i]), float(pf[i])
    mask = (pt > t_a + FAN_T_MIN) & (pt < t_a + FAN_T_MAX)
    cand = np.where(mask)[0]
    cand = cand[np.argsort(pt[cand])]
    lines = [(t_a, f_a, float(pt[j]), float(pf[j])) for j in cand[:FAN_FANOUT]]
    return (t_a, f_a), lines

def style_axes(fig, fmin, fmax, row=None, col=None, times=None):
    ykw = (dict(type="log", range=[math.log10(max(1, fmin)), math.log10(fmax)])
           if USE_LOG_Y else dict(type="linear", range=[fmin, fmax]))
    tk = _nice_tick_params(times)
    xkw = dict(showline=True, mirror=True, ticks="outside", showgrid=True,
               tickmode="linear", dtick=tk["dtick"], tick0=tk["tick0"], tickformat=".0f")
    fig.update_yaxes(**ykw, showgrid=True, zeroline=False, row=row, col=col)
    fig.update_xaxes(**xkw, row=row, col=col)

def add_titles(fig, main, sub):
    fig.update_layout(template="plotly_white", width=IMG_W, height=IMG_H,
                      paper_bgcolor="white", plot_bgcolor="white",
                      margin=dict(l=80, r=30, t=95, b=55))
    fig.add_annotation(text=main, xref="paper", yref="paper", x=0, y=1.15,
                       showarrow=False, font=dict(size=22, color="#1f2a44"))
    fig.add_annotation(text=sub, xref="paper", yref="paper", x=0, y=1.08,
                       showarrow=False, font=dict(size=14, color="#324a66"))

# ================== PLOT DE 1 BLOCO ==================
def plot_block(row, out_dir, dual=True, overlay=True):
    # blobs
    S_blk  = bytes_to_ndarray(row.get("stft_bytes"))
    freqs  = bytes_to_ndarray(row.get("freqs_bytes"))
    times  = bytes_to_ndarray(row.get("times_bytes"))
    if S_blk.size == 0: raise ValueError("stft_bytes vazio")

    # correções e recorte Y
    S_db, freqs, times, zlim = detect_scale_and_fix(S_blk, freqs, times)
    fmin, fmax = YLIM_HZ
    freqs = np.maximum(freqs, 0.0)
    band = (freqs >= fmin) & (freqs <= fmax)
    S_show, F_show = S_db[band, :], freqs[band]

    # picos
    if AUTO_PEAK_DENSITY:
        pt, pf = estimate_peaks_auto_density(S_db, freqs, times)
    else:
        pt, pf = _peaks_with_percentile(S_db, freqs, times, pctl=95.0)
    if pf.size:
        sel = (pf >= fmin) & (pf <= fmax)
        pf, pt = pf[sel], pt[sel]

    # metadados (copiados do parquet)
    title = row.get("title", "Desconhecida")
    val, aro = row.get("valence", None), row.get("arousal", None)
    emo = row.get("emotion_label", None)
    nfft = int(row.get("stft_n_fft", 2048) or 2048)
    hop  = int(row.get("stft_hop",   512)  or 512)
    win  = str(row.get("stft_window", "hann"))

    main = f"{TITLE_PREFIX}{title}"
    sub  = f"Bloco {int(row['block_idx'])} — STFT {win} {nfft}/{hop}"
    if pd.notna(val) and pd.notna(aro): sub += f" — Valência {val:.3f}, Arousal {aro:.3f}"
    if isinstance(emo, str) and emo:    sub += f" — Rótulo: {emo}"

    blk = int(row["block_idx"])
    base = os.path.join(out_dir, f"block_{blk:04d}")
    ensure_dir(out_dir)

    anchor_info, lines = select_anchor_and_targets(pt, pf)

    # Dual
    if dual:
        fig = make_subplots(rows=1, cols=2, column_widths=[0.6, 0.4], horizontal_spacing=0.08)
        fig.add_trace(go.Heatmap(z=S_show, x=times, y=F_show, colorscale=SPEC_CMAP,
                                 zmin=zlim[0], zmax=zlim[1],
                                 colorbar=dict(title="Magnitude (dB)", thickness=14, x=1.02)),
                      row=1, col=1)
        fig.add_trace(go.Scatter(x=pt, y=pf, mode="markers", marker=PK_MARKER, name="Picos"),
                      row=1, col=2)
        if anchor_info:
            t_a, f_a = anchor_info
            fig.add_shape(type="circle", x0=t_a-0.08, x1=t_a+0.08, y0=f_a-200, y1=f_a+200,
                          line=dict(color="black", width=1.5), row=1, col=2)
            if SHOW_FAN_LINES:
                for (x0, y0, x1, y1) in lines:
                    fig.add_shape(type="line", x0=x0, y0=y0, x1=x1, y1=y1,
                                  line=dict(width=1, color="rgba(0,0,0,0.45)"), row=1, col=2)
        style_axes(fig, fmin, fmax, row=1, col=1, times=times)
        style_axes(fig, fmin, fmax, row=1, col=2, times=times)
        add_titles(fig, main, sub)
        if EXPORT_HTML:
            fig.write_html(base + "_dual.html", include_plotlyjs="cdn")

    # Overlay
    if overlay:
        fig2 = make_subplots(rows=1, cols=1)
        fig2.add_trace(go.Heatmap(z=S_show, x=times, y=F_show, colorscale=SPEC_CMAP,
                                  zmin=zlim[0], zmax=zlim[1],
                                  colorbar=dict(title="Magnitude (dB)", thickness=14, x=1.02)))
        fig2.add_trace(go.Scatter(x=pt, y=pf, mode="markers", marker=PK_MARKER, name="Picos"))
        if anchor_info:
            t_a, f_a = anchor_info
            fig2.add_shape(type="circle", x0=t_a-0.08, x1=t_a+0.08, y0=f_a-200, y1=f_a+200,
                           line=dict(color="black", width=1.5))
            if SHOW_FAN_LINES:
                for (x0, y0, x1, y1) in lines:
                    fig2.add_shape(type="line", x0=x0, y0=y0, x1=x1, y1=y1,
                                   line=dict(width=1, color="rgba(0,0,0,0.45)"))
        style_axes(fig2, fmin, fmax, row=1, col=1, times=times)
        add_titles(fig2, main, sub + " — Overlay")
        if EXPORT_HTML:
            fig2.write_html(base + "_overlay.html", include_plotlyjs="cdn")

    # DF de picos (inclui VA/label do bloco p/ validação)
    n = len(pt)
    return pd.DataFrame({
        "song_id":       [row.get("song_id")] * n,
        "block_idx":     [blk] * n,
        "time_s":        pt.astype(float) if n else np.array([], dtype=float),
        "freq_hz":       pf.astype(float) if n else np.array([], dtype=float),
        "title":         [title] * n,
        "valence":       [val] * n,
        "arousal":       [aro] * n,
        "emotion_label": [emo] * n
    })

# ================ UTIL DE I/O ================
def _iter_song_parquets(in_path):
    """
    Retorna lista de (song_path, song_id_str) a partir de:
      - diretório com *.parquet
      - OU caminho para um único parquet
    """
    p = pathlib.Path(in_path)
    if p.is_dir():
        files = sorted(p.glob("song_*.parquet"))
    else:
        files = [p]
    out = []
    for fp in files:
        m = re.search(r"song_(\d+)\.parquet$", fp.name)
        sid = m.group(1) if m else fp.stem
        out.append((str(fp), sid))
    return out

# ================ LOOP PRINCIPAL ================
def process_all_songs():
    songs = _iter_song_parquets(IN_PATH)
    if not songs:
        print(f"[ERRO] Nenhum parquet encontrado em: {IN_PATH}")
        return

    song_iter = tqdm(songs, desc="Songs", unit="song") if tqdm else songs
    all_index_rows = []

    for song_path, song_id_str in song_iter:
        try:
            df = pd.read_parquet(song_path)
        except Exception as e:
            print(f"\n[ERRO] Song {song_id_str}: falha ao ler parquet: {e}")
            continue

        # normaliza e ordena
        df["block_idx"] = pd.to_numeric(df["block_idx"], errors="coerce").astype("Int64")
        df = df.sort_values("block_idx").reset_index(drop=True)

        # pasta por música
        try:
            song_id  = int(df.loc[df["block_idx"].idxmin(), "song_id"]) if "song_id" in df else int(song_id_str)
        except Exception:
            song_id = int(song_id_str) if song_id_str.isdigit() else 0
        song_tit = str(df.loc[df["block_idx"].idxmin(), "title"]) if "title" in df else "Desconhecida"
        song_dir = os.path.join(OUT_ROOT, f"{song_id:04d}_{slugify(song_tit)}")
        ensure_dir(song_dir)

        # progresso por blocos
        blocks = list(df.itertuples(index=False))
        blk_iter = tqdm(blocks, desc=f"Song {song_id_str}", unit="blk", leave=False) if tqdm else blocks

        peaks_parts = []
        for row in blk_iter:
            row = row._asdict() if hasattr(row, "_asdict") else row
            try:
                dfp = plot_block(row, song_dir, dual=DO_DUAL, overlay=DO_OVERLAY)
                peaks_parts.append(dfp)
            except Exception as e:
                # imprime erro e continua
                print(f"\n[ERRO] Song {song_id_str} bloco {row.get('block_idx')}: {e}")

        # salvar parquet de picos da música
        if peaks_parts:
            peaks_df = pd.concat(peaks_parts, ignore_index=True)
            out_pq   = os.path.join(song_dir, "peaks_all_blocks.parquet")
            peaks_df.to_parquet(out_pq, index=False, compression="snappy")
            all_index_rows.append(dict(song_id=song_id, title=song_tit, peaks_path=out_pq,
                                       n_points=len(peaks_df)))
        else:
            print(f"[WARN] Song {song_id_str}: nenhum pico coletado.")

    # índice geral (opcional)
    if all_index_rows:
        idx_df = pd.DataFrame(all_index_rows).sort_values("song_id")
        ensure_dir(OUT_ROOT)
        idx_path = os.path.join(OUT_ROOT, "peaks_index.parquet")
        idx_df.to_parquet(idx_path, index=False, compression="snappy")
        print(f"\n[OK] Índice de picos salvo em: {idx_path}")
    print("[DONE] Lote concluído.")

# ---- run ----
process_all_songs()


Songs:   0%|          | 0/1497 [00:00<?, ?song/s]

Song 10:   0%|          | 0/4 [00:00<?, ?blk/s]

Song 1000:   0%|          | 0/4 [00:00<?, ?blk/s]

Song 1001:   0%|          | 0/4 [00:00<?, ?blk/s]


[ERRO] Song 1001 bloco 3: stft_bytes vazio


...

Song 1605:   0%|          | 0/4 [00:00<?, ?blk/s]


[ERRO] Song 1605 bloco 3: stft_bytes vazio


Song 1606:   0%|          | 0/4 [00:00<?, ?blk/s]


[ERRO] Song 1606 bloco 3: stft_bytes vazio


Song 1607:   0%|          | 0/4 [00:00<?, ?blk/s]